In [1]:
from model import Tacotron
from utils import TTSDataset, collate_fn
import pandas as pd
from torchaudio import transforms
from torch.utils.data import Dataset, DataLoader
import torch
from torch import nn
from torch.nn.functional import relu
import numpy as np
from torchaudio.functional import deemphasis
import tempfile
import torchaudio

In [2]:
from tqdm import tqdm_notebook as tqdm

In [3]:
from IPython import display
from IPython.display import clear_output

In [4]:
dataset = TTSDataset(resample_rate=24000, num_elements=None)
dataloader = DataLoader(dataset, 32, collate_fn=collate_fn, num_workers=8, shuffle=True)

In [5]:
def reconstruct_audio(spectrogram):
    spectrogram = (torch.clip(spectrogram, 0, 1)*100) - 80
    spectrogram = torch.pow(10, spectrogram*0.05)
    transform = transforms.GriffinLim(n_fft=2048, win_length=int(24000*0.05), hop_length=int(24000*0.0125), power=1.5)
    waveform = transform(spectrogram).detach()
    waveform = deemphasis(waveform)
    return waveform

In [6]:
def code_text(text):
    text = dataset.preprocessor.transform_single_text(text)
    text = torch.tensor(text).unsqueeze(0)
    return text

In [7]:
def loss(true, pred):
    criterion = nn.L1Loss()
    output = criterion(pred, true)
    return output

In [8]:
spec = next(iter(dataloader))[3]
spec.shape

torch.Size([32, 1025, 538])

In [9]:
display.Audio(reconstruct_audio(spec)[0].numpy(), rate=24000)

In [9]:
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

In [10]:
model = Tacotron(38)
model.load_state_dict(torch.load('../tacotron_vw/epoch_680_train_result'))

<All keys matched successfully>

In [11]:
import os
if 'metrics.csv' not in os.listdir():
    metric_frame = pd.DataFrame({
        'epoch':[],
        'loss_value':[]
    }).to_csv('metrics.csv', index=False)
metrics_frame = pd.read_csv('metrics.csv', index_col=False)

In [12]:
metrics_frame.shape

(686, 2)

In [13]:
NUM_EPOCHS = 800
train_loss = []
test_loss = []
optimizer = torch.optim.Adam(model.parameters(), lr = 1e-4)

In [50]:
model.to(device)
for epoch in range(700, NUM_EPOCHS):
    model.train()
    epoch_train_losses = []
    for text, audio, mel, spectrogram in tqdm(dataloader):
        text = text.to(device)
        mel = mel.to(device)
        spectrogram = spectrogram.to(device)
        model.zero_grad()
        pred_mel, pred_spec = model(text, mel)
        pred_spec = pred_spec.transpose(1,2)
        loss_mel = loss(mel, pred_mel)
        loss_spec = loss(spectrogram, pred_spec)
        final_loss = 0.5 * loss_spec + 0.5 * loss_mel
        final_loss.backward()
        nn.utils.clip_grad_norm(model.parameters(), 1.)
        optimizer.step()
        epoch_train_losses.append(final_loss.cpu().detach().numpy())
    if epoch%10==0:
        with torch.no_grad():
            sample_text = code_text("Привет Это проверка генерации речи из текста!")
            model.eval()
            model.to('cpu')
            test_spec = reconstruct_audio(model.predict(sample_text))
            with tempfile.TemporaryDirectory() as tempdir:
                path = f"save_example_{epoch}.wav"
                torchaudio.save(path, test_spec, 24000)
            model.to(device)
        torch.save(model.state_dict(), f"epoch_{epoch}_train_result")
    metrics_frame.loc[epoch] = np.mean(epoch_train_losses)
    metrics_frame.to_csv('metrics.csv', index=False)
    print(epoch, np.mean(epoch_train_losses))

C:\Users\yakub\AppData\Local\Temp\ipykernel_12840\1405509394.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for text, audio, mel, spectrogram in tqdm(dataloader):


  0%|          | 0/509 [00:00<?, ?it/s]

C:\Users\yakub\AppData\Local\Temp\ipykernel_12840\1405509394.py:16: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(model.parameters(), 1.)


700 0.032638874


  0%|          | 0/509 [00:00<?, ?it/s]

...

C:\Users\yakub\AppData\Local\Temp\ipykernel_12840\1405509394.py:16: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(model.parameters(), 1.)


791 0.032421585


C:\Users\yakub\AppData\Local\Temp\ipykernel_12840\1405509394.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for text, audio, mel, spectrogram in tqdm(dataloader):


  0%|          | 0/509 [00:00<?, ?it/s]

C:\Users\yakub\AppData\Local\Temp\ipykernel_12840\1405509394.py:16: UserWarning: torch.nn.utils.clip_grad_norm is now deprecated in favor of torch.nn.utils.clip_grad_norm_.
  nn.utils.clip_grad_norm(model.parameters(), 1.)


In [49]:
sample_text = code_text("Ровно три года назад у вокзала стояла голая девушка и позволяла трогать себа за левую грудь.")
model.to('cpu')
model.eval()
test_spec = reconstruct_audio(model.predict(sample_text))
with tempfile.TemporaryDirectory() as tempdir:
    path = f"teeeest.wav"
    torchaudio.save(path, test_spec, 24000)

In [13]:
model.train()
sample_text = code_text("Как незнайка оказался на луне?")
model.to('cpu')
test_spec = reconstruct_audio(model.predict(sample_text))
# with tempfile.TemporaryDirectory() as tempdir:
#     path = f"save_example_{epoch}.wav"
#     torchaudio.save(path, test_spec, 24000)

In [56]:
display.Audio(test_spec.numpy(), rate=24000)

In [19]:
loss_mel

tensor(1.8905, device='cuda:0', grad_fn=<MeanBackward0>)

In [20]:
loss_spec

tensor(0.0354, device='cuda:0', grad_fn=<MeanBackward0>)

In [45]:
test_spec.abs()

tensor([[5.8682e-04, 8.7431e-04, 7.9268e-04,  ..., 1.6969e-06, 2.0844e-06,
         1.5385e-06]])

In [ ]:
С тревожным чувством берусь я за перо.

In [40]:
sample_text = code_text("Привет! Это проверка генерации речи из текста!")
model.to('cpu')
model.eval()

Tacotron(
  (encoder): TacotronEncoder(
    (char_embedding): Embedding(38, 256)
    (encoder_prenet): Sequential(
      (0): Linear(in_features=256, out_features=256, bias=True)
      (1): Dropout(p=0.5, inplace=False)
      (2): Linear(in_features=256, out_features=128, bias=True)
      (3): Dropout(p=0.5, inplace=False)
    )
    (CBHD): EncoderCBHD(
      (convolve_sets): ModuleList(
        (0): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 0), value=0)
            (1): Conv1d(128, 128, kernel_size=(1,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          )
        )
        (1): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 1), value=0)
            (1): Conv1d(128, 128, kernel_size=(2,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, e

In [41]:
test_audio = reconstruct_audio(model.predict(sample_text))

In [42]:
test_audio

tensor([[ 5.0051e-04, -9.9959e-04, -2.2230e-03,  ..., -1.6136e-05,
         -1.1925e-05, -9.9754e-06]])

In [46]:
display.Audio(test_audio.abs()[0].numpy(), rate=24000)

In [33]:
loss_mel

tensor(874.6371, device='cuda:0', grad_fn=<MeanBackward0>)

In [34]:
loss_spec

tensor(10.9902, device='cuda:0', grad_fn=<MeanBackward0>)

In [17]:
spectrogram

tensor([[[ -66.2601,  -81.4281,  -74.2407,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -66.4388,  -70.5101,  -69.3915,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -66.8526,  -70.0612,  -67.6829,  ..., -100.0000, -100.0000,
          -100.0000],
         ...,
         [ -52.0097,  -51.1252,  -59.6431,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -66.3263,  -54.3086,  -57.9520,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -76.9271,  -57.7109,  -57.5889,  ..., -100.0000, -100.0000,
          -100.0000]],

        [[ -82.9806,  -89.9874, -100.0000,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -83.0703,  -90.1837, -100.0000,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -83.0809,  -90.7176, -100.0000,  ..., -100.0000, -100.0000,
          -100.0000],
         ...,
         [ -49.0506,  -56.2065,  -53.1666,  ..., -100.0000, -100.0000,
          -100.0000],
         [ -48.8502,  -55.8873,  -52.919

In [18]:
pred_spec

tensor([[[ -62.2363,  -77.3947,  -85.8708,  ..., -100.0043, -100.0032,
          -100.0043],
         [ -61.3311,  -76.2063,  -83.7461,  ..., -100.0084, -100.0081,
          -100.0084],
         [ -60.5917,  -75.0856,  -82.0439,  ..., -100.0244, -100.0204,
          -100.0244],
         ...,
         [ -49.8313,  -63.9831,  -70.8464,  ...,  -99.9781,  -99.9824,
           -99.9781],
         [ -49.7358,  -64.2959,  -70.9207,  ...,  -99.9793,  -99.9750,
           -99.9793],
         [ -50.6218,  -64.9588,  -71.9419,  ...,  -99.9991,  -99.9964,
           -99.9991]],

        [[ -61.3475,  -76.8347,  -87.2627,  ..., -100.0020, -100.0021,
          -100.0024],
         [ -60.4987,  -75.6955,  -85.6668,  ..., -100.0058, -100.0068,
          -100.0062],
         [ -59.7536,  -74.4733,  -83.7902,  ..., -100.0225, -100.0199,
          -100.0228],
         ...,
         [ -50.0605,  -64.1179,  -74.7696,  ...,  -99.9754,  -99.9811,
           -99.9763],
         [ -49.8314,  -64.3668,  -74.890

In [24]:
test_spec.max()

tensor(0.0514)

In [23]:
audio.max()

tensor(0.4296)

In [26]:
np.mean(epoch_train_losses)

In [27]:
print(epoch_train_losses)

In [15]:
ttt = model.to('cpu').predict(sample_text)

In [17]:
ttt.shape

torch.Size([1, 1025, 2495])

In [20]:
reconstruct_audio(ttt).max()

tensor(0.0359)

In [25]:
display.Audio(reconstruct_audio(ttt)[0].numpy(), rate=24000)

NameError: name 'ttt' is not defined

In [ ]:
with tempfile.TemporaryDirectory() as tempdir:
                path = f"save_example_{epoch}.wav"
                torchaudio.save(path, test_spec, 24000)

In [15]:
sample_text = code_text("как дела!")
test_sample = model.to('cpu').predict(sample_text)
# test_spec = reconstruct_audio(relu(model.predict(sample_text)))
# display.Audio(test_spec[0].cpu().numpy(), rate=12000)

In [19]:
test_sample.shape

torch.Size([1, 1025, 2495])

In [19]:
model

Tacotron(
  (encoder): TacotronEncoder(
    (char_embedding): Embedding(38, 256)
    (encoder_prenet): Sequential(
      (0): Linear(in_features=256, out_features=256, bias=True)
      (1): Dropout(p=0.5, inplace=False)
      (2): Linear(in_features=256, out_features=128, bias=True)
      (3): Dropout(p=0.5, inplace=False)
    )
    (CBHD): EncoderCBHD(
      (convolve_sets): ModuleList(
        (0): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 0), value=0)
            (1): Conv1d(128, 128, kernel_size=(1,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          )
        )
        (1): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 1), value=0)
            (1): Conv1d(128, 128, kernel_size=(2,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, e

In [28]:
test_sample.shape

torch.Size([1, 1025, 2495])

In [ ]:
pred_spec.shape

In [15]:
np.mean(epoch_train_losses)

67.20557

In [21]:
code_text("С тревожным чувсвом")

tensor([[23,  0, 24, 22, 11,  8, 20, 12, 19, 33, 18,  0, 29, 25,  8, 23,  8, 20,
         18]])

In [ ]:
next(iter(dataloader))[2].shape

In [ ]:
spectrogram.shape

In [ ]:
pred_spec.shape

In [23]:
model.to(device)

Tacotron(
  (encoder): TacotronEncoder(
    (char_embedding): Embedding(38, 256)
    (encoder_prenet): Sequential(
      (0): Linear(in_features=256, out_features=256, bias=True)
      (1): Dropout(p=0.5, inplace=False)
      (2): Linear(in_features=256, out_features=128, bias=True)
      (3): Dropout(p=0.5, inplace=False)
    )
    (CBHD): EncoderCBHD(
      (convolve_sets): ModuleList(
        (0): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 0), value=0)
            (1): Conv1d(128, 128, kernel_size=(1,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          )
        )
        (1): BatchNormConvolution(
          (batchnorm): Sequential(
            (0): ConstantPad1d(padding=(0, 1), value=0)
            (1): Conv1d(128, 128, kernel_size=(2,), stride=(1,), bias=False)
            (2): ReLU()
            (3): BatchNorm1d(128, e

In [ ]:
with torch.no_grad():
            sample_text = code_text("Привет! Это проверка генерации речи из текста!")
            model.to('cpu')
            test_spec = reconstruct_audio(torch.clamp(model.predict(sample_text), min=1e-5))
            with tempfile.TemporaryDirectory() as tempdir:
                path = f"save_example_{epoch}.wav"
                torchaudio.save(path, test_spec, 24000)
            model.to(device)
        torch.save(model.state_dict(), f"epoch_{epoch}_train_result")

In [ ]:
ttt = next(iter(dataloader))

In [ ]:
ttt[3].min()

In [ ]:
display.Audio(ttt[1][0].numpy(), rate=24000)

In [ ]:
def reconstruct_audio(spectrogram):
    transform = transforms.GriffinLim(n_fft=2048, win_length=int(24000*0.05), hop_length=int(24000*0.0125))
    waveform = transform(spectrogram).detach()
    return waveform

In [ ]:
def code_text(text):
    text = dataset.preprocessor.transform_single_text(text)
    text = torch.tensor(text).unsqueeze(0)
    return text

In [ ]:
sample_text = code_text("Привет! Это проверка генерации речи из текста!")

In [ ]:
model = Tacotron(38)

In [ ]:
model.predict(sample_text)

In [ ]:
from torch.nn.functional import relu

In [ ]:
model.predict(sample_text).shape

In [ ]:
ttt[3].shape

In [ ]:
relu = torch.nn.ReLU()

In [ ]:
specs = reconstruct_audio(relu(model.predict(sample_text)))


In [ ]:
specs

In [ ]:
display.Audio(specs[0].numpy(), rate=24000)
display.Audio(specs[0].numpy(), rate=24000)

In [ ]:
specs[0]